In [1]:
import pandas as pd
import numpy as np

In [2]:
import os
path="/Users/jesperdybkjaer/Documents/DTU/Kandidat/4.semester/3_SocialDataanalysisAndVisualization/Final_project"
os.chdir(path)

In [3]:
# import the data
df = pd.read_csv("trae_basis.csv")

/Users/jesperdybkjaer/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3058: DtypeWarning: Columns (6,41,46,47,48,49,50,62,64,65,69,71,73,76,79,83,89,103,117,122,135,136,137,147,156,157,158,167,168,174,175,176,177,178,179,180,181) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [4]:
# Focus features
# ['slaegtsnavn','planteaar','ejer','trae_historie','donor','bydel_nr', 'name','geometry', 'tree_sum','X','Y',]

Get the x and y values in seperate columns for all trees, and creating a geometry point (wkb_geometry is a string).

In [82]:
df['X']=np.zeros(len(df))
df['Y']=np.zeros(len(df))

for i in range(len(df)):
    temp = df['wkb_geometry'][i].split()
    df['X'][i]=float(temp[1][1:])
    df['Y'][i]=float(temp[2][:-1])

##Creating a geometry point of our data
df = gpd.GeoDataFrame(df, geometry=gpd.points_from_xy(df.X,df.Y))


/Users/jesperdybkjaer/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/Users/jesperdybkjaer/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


In [83]:
### Sort the data the same way as Andreas
#Drop the city names which are not given
print(f'Dataset with all observations: {df.shape}')

df_neighbourhood = df[df.bydelsnavn.notna()]
print(f'Dataset with neighbourhood: {df_neighbourhood.shape}')

#Drop the tree names which are not given

df_withtype = df[df.slaegtsnavn.notna()]
print(f'Dataset with treetype: {df_withtype.shape}')

#Remove the non registred trees so it is nicer to look at

df_withtype = df_withtype[df_withtype['slaegtsnavn'] != 'Ikke registreret']

Dataset with all observations: (59580, 186)
Dataset with neighbourhood: (57006, 186)
Dataset with treetype: (59557, 186)


# Map with bokeh
Inspirations from:
https://towardsdatascience.com/walkthrough-mapping-basics-with-bokeh-and-geopandas-in-python-43f40aa5b7e9

Dashboard/on page:
https://towardsdatascience.com/https-medium-com-radecicdario-next-level-data-visualization-dashboard-app-with-bokeh-flask-c588c9398f98

In [7]:
#import main Python libaries
import numpy as np
import pandas as pd
import shapefile as shp
import matplotlib.pyplot as plt
import seaborn as sns
import urllib.request

#initialize visualization setup
sns.set(style='whitegrid', palette='pastel', color_codes=True)
sns.mpl.rc('figure', figsize=(10,6))
%matplotlib inline

### Shapefiles of Copenhagen neighbourhoods

Import the shape files of copenhagen.

In [8]:
import urllib, geojson, gdal, subprocess

# Import shapefile from github:
# https://github.com/codeforamerica/click_that_hood/blob/master/public/data/copenhagen.geojson
url = 'https://raw.githubusercontent.com/codeforamerica/click_that_hood/master/public/data/copenhagen.geojson'
response = urllib.request.urlopen(url)
data = geojson.loads(response.read())

with open('data.geojson', 'w', encoding='utf-8') as f:
    geojson.dump(data, f)
    
    
args = ['ogr2ogr', '-f', 'ESRI Shapefile', 'destination_data.shp', 'data.geojson']
subprocess.Popen(args);

In [9]:
# Import geopandas package
import geopandas as gpd

# Read in shapefile and examine data
df_cph = gpd.read_file('destination_data.shp')
df_cph = df_cph.drop(['id','cartodb_id','created_at','updated_at'],axis=1)
df_cph=df_cph.rename(columns={'name':'district'})
df_cph

bydel_nr                   district  \
0         1                   Indre By   
1         2                   Østerbro   
2         5                      Valby   
3         4  Vesterbro-Kongens Enghave   
4         9                 Amager Øst   
5         7             Brønshøj-Husum   
6         3                   Nørrebro   
7         8                 Bispebjerg   
8         6                    Vanløse   
9        10                Amager Vest   

                                            geometry  
0  POLYGON ((12.61149 55.69763, 12.61534 55.69783...  
1  POLYGON ((12.61591 55.72065, 12.62000 55.72348...  
2  POLYGON ((12.52434 55.66666, 12.52449 55.66668...  
3  POLYGON ((12.54446 55.64038, 12.54446 55.64038...  
4  POLYGON ((12.63094 55.67050, 12.63126 55.67028...  
5  POLYGON ((12.46894 55.69976, 12.46698 55.70024...  
6  POLYGON ((12.56165 55.69667, 12.56152 55.69636...  
7  POLYGON ((12.51594 55.70664, 12.51539 55.70693...  
8  POLYGON ((12.46894 55.69976, 12.46935 55.69965...  
9  POLYGON ((12.58271 55.66850, 12.58661 55.66783...

In [10]:
# Create dataframe with sum of trees in different neigbourhoods
df_tree_sum=df_neighbourhood.groupby('bydelsnavn')['id'].count()
df_tree_sum=pd.DataFrame(df_tree_sum,columns=['id'])
df_tree_sum=df_tree_sum.rename(columns={'id':'tree_sum'})

## Befolkning pr. 31 jan 2019: https://statistikbanken.kk.dk/1050dc07-e88c-4206-ae4e-645718e26ab9/ReportSection
district1 = ['Indre By', 'Østerbro','Nørrebro','Vesterbro-Kongens Enghave','Valby','Vanløse',
        'Brønshøj-Husum','Bispebjerg','Amager Øst','Amager Vest']
population = [55866,79803,80254,72688,60308,41195,44784,55172,59803,78973]
temp1 = pd.DataFrame({'district':district1,'population':population})

# Area of neighbourhoods
district3 = ['Indre By','Østerbro','Nørrebro','Vesterbro-Kongens Enghave','Valby',
            'Vanløse','Brønshøj-Husum','Bispebjerg','Amager Øst','Amager Vest']
area = [9,8.7,4.1,8.2,9.2,6.7,8.7,6.8,9.1,19.2] # area in km^2
temp3 = pd.DataFrame({'district':district3,'area':area})

# Merge the dataframes together
df_cph=df_cph.merge(df_tree_sum,left_on='district',right_on=df_tree_sum.index)
df_cph=df_cph.merge(temp1,left_on='district',right_on='district')
df_cph=df_cph.merge(temp3,left_on='district',right_on='district')
df_cph

bydel_nr                   district  \
0         1                   Indre By   
1         2                   Østerbro   
2         5                      Valby   
3         4  Vesterbro-Kongens Enghave   
4         9                 Amager Øst   
5         7             Brønshøj-Husum   
6         3                   Nørrebro   
7         8                 Bispebjerg   
8         6                    Vanløse   
9        10                Amager Vest   

                                            geometry  tree_sum  population  \
0  POLYGON ((12.61149 55.69763, 12.61534 55.69783...      6105       55866   
1  POLYGON ((12.61591 55.72065, 12.62000 55.72348...      7824       79803   
2  POLYGON ((12.52434 55.66666, 12.52449 55.66668...      4878       60308   
3  POLYGON ((12.54446 55.64038, 12.54446 55.64038...      6679       72688   
4  POLYGON ((12.63094 55.67050, 12.63126 55.67028...      3930       59803   
5  POLYGON ((12.46894 55.69976, 12.46698 55.70024...      4160       44784   
6  POLYGON ((12.56165 55.69667, 12.56152 55.69636...      6770       80254   
7  POLYGON ((12.51594 55.70664, 12.51539 55.70693...      8268       55172   
8  POLYGON ((12.46894 55.69976, 12.46935 55.69965...      3915       41195   
9  POLYGON ((12.58271 55.66850, 12.58661 55.66783...      4477       78973   

   area  
0   9.0  
1   8.7  
2   9.2  
3   8.2  
4   9.1  
5   8.7  
6   4.1  
7   6.8  
8   6.7  
9  19.2

We can now convert the data of the districts to a format that is conducive to mapping.

In [11]:
import json
from bokeh.io import show
from bokeh.models import (CDSView, ColorBar, ColumnDataSource,
                          CustomJS, CustomJSFilter, 
                          GeoJSONDataSource, HoverTool,
                          LinearColorMapper, Slider)
from bokeh.layouts import column, row, widgetbox
from bokeh.palettes import brewer
from bokeh.plotting import figure

In [12]:
# Input GeoJSON source that contains features for plotting
#geosource = GeoJSONDataSource(geojson = df2.to_json(default_handler=str)) # If it print this a error try use this
geosource = GeoJSONDataSource(geojson = df_cph.to_json())

Correct format, now ready to plot in Bokeh.

In [13]:
from bokeh.io import push_notebook, show, output_notebook
from bokeh.layouts import row
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, ranges, Legend
from bokeh.models.ranges import FactorRange

output_notebook()

Loading BokehJS ...

Define the colorbar for number of trees for all bokeh maps

In [22]:
# Define color palettes
palette = brewer['BuGn'][8]
palette = palette[::-1] # reverse order of colors so higher values have darker colors

# Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
color_mapper = LinearColorMapper(palette = palette, low = 0, high = 9000)

# Define custom tick labels for color bar.
tick_labels = {'0': '0', '1000': '1000',
 '2000':'2000', '3000':'3000',
 '4000':'4000', '5000':'5000','6000':'6000','7000':'7000','8000':'8000','9000':'9000'}

# Create color bar.
color_bar = ColorBar(color_mapper = color_mapper, 
                     label_standoff = 8,
                     width = 500, height = 20,
                     border_line_color = None,
                     location = (0,0), 
                     orientation = 'horizontal',
                     major_label_overrides = tick_labels)


# First map on webpage

In [23]:
# Create figure object.
p = figure(title = 'Trees in Copenhagen neighbourhoods', 
           plot_height = 800 ,
           plot_width = 800, 
           toolbar_location = 'below',
           tools = 'pan, wheel_zoom, box_zoom, reset',
           match_aspect=True)

p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

# Add patch renderer to figure.
neighbourhoods = p.patches('xs','ys', source = geosource,
                   fill_color = {'field' :'tree_sum',
                                 'transform' : color_mapper},
                   line_color = 'gray', 
                   line_width = 0.25, 
                   fill_alpha = 1)

# Create hover tool
p.add_tools(HoverTool(renderers = [neighbourhoods],
                      tooltips = [('Neighbourhood','@district'),
                                ('Number of trees','@tree_sum'),
                                 ('Population','@population'),
                                 ('Area [km^2]','@area{0.0}')]))

p.add_layout(color_bar, 'below')

show(p)

## We are now interested to add some trees

# ALL trees

In [24]:
print(f'Number of trees: {len(df)}')

Number of trees: 59580


In [25]:
# Create figure object.
p1 = figure(title = 'Trees in Copenhagen neighbourhoods', 
           plot_height = 800 ,
           plot_width = 800, 
           toolbar_location = 'below',
           tools = 'pan, wheel_zoom, box_zoom, reset',
           match_aspect=True)

p1.xgrid.grid_line_color = None
p1.ygrid.grid_line_color = None

# Add patch renderer to figure.
neighbourhoods = p1.patches('xs','ys', source = geosource,
                   fill_color = {'field' :'tree_sum',
                                 'transform' : color_mapper},
                   line_color = 'gray', 
                   line_width = 0.25, 
                   fill_alpha = 1)

# Create hover tool
p1.add_tools(HoverTool(renderers = [neighbourhoods],
                      tooltips = [('Neighbourhood','@district')
#                                ,('Number of trees','@tree_sum')
#                                 ,('Population','@population')
#                                 ,('Area [km^2]','@area{0.0}')
                                 ]))

# Draw the coordinates as circles
p1.circle(x=df['X'], y=df['Y'],
           color='red', size=1, alpha=0.9)


# Specify layout
p1.add_layout(color_bar, 'below')
show(p1)

# ALL with neighbourhood

In [27]:
print(f'Number of trees: {len(df)}')
print(f'Number of trees with neighbourhood: {len(df_neighbourhood)}')

Number of trees: 59580
Number of trees with neighbourhood: 57006


In [28]:
# Create figure object.
p2 = figure(title = 'Trees in Copenhagen neighbourhoods', 
           plot_height = 800 ,
           plot_width = 800, 
           toolbar_location = 'below',
           tools = 'pan, wheel_zoom, box_zoom, reset',
           match_aspect=True)

p2.xgrid.grid_line_color = None
p2.ygrid.grid_line_color = None

# Add patch renderer to figure.
neighbourhoods = p2.patches('xs','ys', source = geosource,
                   fill_color = {'field' :'tree_sum',
                                 'transform' : color_mapper},
                   line_color = 'gray', 
                   line_width = 0.25, 
                   fill_alpha = 1)

# Create hover tool
p2.add_tools(HoverTool(renderers = [neighbourhoods],
                      tooltips = [('Neighbourhood','@district')
#                                ,('Number of trees','@tree_sum')
#                                 ,('Population','@population')
#                                 ,('Area [km^2]','@area{0.0}')
                                 ]))

# Draw the coordinates as circles
p2.circle(x=df_neighbourhood['X'], y=df_neighbourhood['Y'],
           color='red', size=1, alpha=0.9)


# Specify layout
p2.add_layout(color_bar, 'below')
show(p2)

# ALL with a tree type

In [30]:
print(f'Number of trees: {len(df)}')
print(f'Number of trees with neighbourhood: {len(df_neighbourhood)}')
print(f'Number of trees with tree type: {len(df_withtype)}')

Number of trees: 59580
Number of trees with neighbourhood: 57006
Number of trees with tree type: 29751


In [31]:
# Create figure object.
p2 = figure(title = 'Trees in Copenhagen neighbourhoods', 
           plot_height = 800 ,
           plot_width = 800, 
           toolbar_location = 'below',
           tools = 'pan, wheel_zoom, box_zoom, reset',
           match_aspect=True)

p2.xgrid.grid_line_color = None
p2.ygrid.grid_line_color = None

# Add patch renderer to figure.
neighbourhoods = p2.patches('xs','ys', source = geosource,
                   fill_color = {'field' :'tree_sum',
                                 'transform' : color_mapper},
                   line_color = 'gray', 
                   line_width = 0.25, 
                   fill_alpha = 1)

# Create hover tool
p2.add_tools(HoverTool(renderers = [neighbourhoods],
                      tooltips = [('Neighbourhood','@district')
#                                ,('Number of trees','@tree_sum')
#                                 ,('Population','@population')
#                                 ,('Area [km^2]','@area{0.0}')
                                 ]))

# Draw the coordinates as circles
p2.circle(x=df_withtype['X'], y=df_withtype['Y'],
           color='red', size=1, alpha=0.9)


# Specify layout
p2.add_layout(color_bar, 'below')
show(p2)

# Most lonely tree

A function is created below to find the tree that is the most lonely.

In [198]:
def dist_point(Point):
    #Point(0,0).distance(Point(1,1))
    
    alltimebest = 0
    for indexP1,P1 in enumerate(Point):
        nearest = 100000
        #print('New: ',indexP1)
        for indexP2, P2 in enumerate(Point):
            if indexP1 != indexP2:
                distance = P1.distance(P2)
                if distance < nearest:
                    nearest = distance
                    index_nearest = indexP2
                    #print(f'update: {nearest}')
                if alltimebest > nearest:
                    break
        if nearest > alltimebest:
            alltimebest = nearest
            #print(indexP1,' ', index_nearest)
            #print(f'AllBest: {alltimebest}')
            index_trees = [Point.index[indexP1],Point.index[index_nearest]]
    return alltimebest,index_trees

To find the distance in meters we need to do the following calculation with the package pyproj.

In [181]:
# TEST SIZE, the loneliest tree is placed on Amager Vest
a=df[df['bydelsnavn']=='Amager Vest']

In [182]:
len(a.geometry)

4477

In [185]:
# without the correct index

import time
#Calculating the distance to nearest neighbour tree

start_time = time.time()
#Distance_to_nearest, trees_index = dist_point(df_tree_cph, V)
alltimebest,index_trees = dist_point(a.geometry)
print("--- %s seconds ---" % (time.time() - start_time))
print(alltimebest,index_trees)

0   1
AllBest: 3.2539536868528754e-05
2   1
AllBest: 3.627803196213247e-05
3   5
AllBest: 4.963140577055925e-05
11   928
AllBest: 8.609242587727083e-05
12   1500
AllBest: 0.00017145328469468247
134   135
AllBest: 0.001041243715847129
174   1363
AllBest: 0.0016260798305924398
691   695
AllBest: 0.0023423320505965295
1094   1093
AllBest: 0.003477105729791273
--- 32.18645787239075 seconds ---
0.003477105729791273 [16607, 16606]


In [199]:
import pyproj
geod = pyproj.Geod(ellps='WGS84')

# THE TREE WITH THE LONGEST DISTANCE TO ITS NEAREST NEIGHBOUR.
# 0.003477105729791273 [16607, 16606]
# IT TOOK --- 3082 seconds --- APPR. 50 MINUTES
angle1,angle2,distance = geod.inv(df.X[16607], df.Y[16607],df.X[16606], df.Y[16606])
# 0.003477105729791273
print('Tree with index 16607, has {0:8.4f} meters to nearest neighbour.'.format(distance))

Tree with index 16607, has 341.3832 meters to nearest neighbour.


In [200]:
# Create figure object.
p = figure(title = 'Trees in Copenhagen neighbourhoods', 
           plot_height = 600 ,
           plot_width = 600, 
           toolbar_location = 'below',
           tools = 'pan, wheel_zoom, box_zoom, reset',
           match_aspect=True)

p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

# Add patch renderer to figure.
neighbourhoods = p.patches('xs','ys', source = geosource,
                   fill_color = {'field' :'tree_sum',
                                 'transform' : color_mapper},
                   line_color = 'gray', 
                   line_width = 0.25, 
                   fill_alpha = 1)

# Draw the coordinates as circles
p.circle(x=df['X'], y=df['Y'],
           color='red', size=1, alpha=0.9)
# Draw the coordinates as circles
p.circle(x=df['X'][16607], y=df['Y'][16607],
           color='blue', size=10, alpha=0.9)
p.circle(x=df['X'][16606], y=df['Y'][16606],
           color='purple', size=5, alpha=0.9)


# Create hover tool
p.add_tools(HoverTool(renderers = [neighbourhoods],
                      tooltips = [('Neighbourhood','@name'),
                                ('Number of trees','@tree_sum')]))

# Specify layout
p.add_layout(color_bar, 'below')
show(p)

The most lonely tree is the blue dot on the map. And is nearest neighbour is the purple dot.
Tree with index 16607, has 341.3832 meters to nearest neighbour.

# Check that we have a geometry point and add features to point

In [ ]:
df_tree_cph['geometry'][0]

In [ ]:
df_tree_cph['geometry'][0]

In [ ]:
df_tree_cph_contig['geometry_point'][0]

In [ ]:
## Read dataframe to geodataframe
#tree_neighbourhood_crs = {'init': 'epsg:4326'}
#tree_neighbourhood_geo = gpd.GeoDataFrame(df_tree_cph,
#                                  crs = tree_neighbourhood_crs,
#                             geometry = df_tree_cph.wkb_geometry_point)
## Get x and y coordinates
#tree_neighbourhood_geo['x'] = [geometry.x for wkb_geometry in tree_neighbourhood_geo['geometry_point']]
#tree_neighbourhood_geo['y'] = [geometry.y for wkb_geometry in tree_neighbourhood_geo['geometry_point']]
#p_df = tree_neighbourhood_geo.drop('geometry_point', axis = 1).copy()
#sitesource = ColumnDataSource(p_df)